Data: [fma](https://github.com/mdeff/fma) fma_small.zip <br>
노래가 들어오면 유사한 노래를 추천 <br>
MFCC, Scaling, DTW

In [1]:
import os
import random
import librosa
from IPython.display import Audio, display
import numpy as np
import multiprocessing as mp
from tqdm.notebook import tqdm
from dtw import accelerated_dtw

5개 데이터만 확인

In [2]:
root_dir = '/hdd/data/adp_data/fma_small/'
dir_list = [os.path.join(root_dir, d) + '/' for d in os.listdir(root_dir)]

random.seed(526)
sample_dirs = random.sample(dir_list, 5)

for dir_path in sample_dirs:
    mp3_files = [f for f in os.listdir(dir_path) if f.endswith('.mp3')]

    if not mp3_files:
        print(f'{dir_path} empty')
        continue

    sample_mp3 = random.choice(mp3_files)
    mp3_path = os.path.join(dir_path, sample_mp3)

    y, sr = librosa.load(mp3_path, sr = None)
    duration = librosa.get_duration(y = y, sr = sr)

    print(f'{mp3_path} 길이: {duration:.2f}초')
    # display(Audio(y, rate = sr))

/hdd/data/adp_data/fma_small/147/147413.mp3 길이: 29.98초
/hdd/data/adp_data/fma_small/141/141310.mp3 길이: 29.98초
/hdd/data/adp_data/fma_small/093/093943.mp3 길이: 29.98초
/hdd/data/adp_data/fma_small/142/142358.mp3 길이: 30.00초
/hdd/data/adp_data/fma_small/038/038879.mp3 길이: 30.00초


mfcc진행 후 Scaling

In [3]:
root_dir = '/hdd/data/adp_data/fma_small/'

def collect_mp3_paths(root_dir):
    mp3_paths = []
    for subdir in os.listdir(root_dir):
        full_subdir = os.path.join(root_dir, subdir)
        if os.path.isdir(full_subdir):
            for file in os.listdir(full_subdir):
                if file.endswith('.mp3'):
                    mp3_paths.append(os.path.join(full_subdir, file))
    return mp3_paths

In [4]:
def z_score_normalize(mfcc):
    mean = np.mean(mfcc, axis = 1, keepdims = True)
    std = np.std(mfcc, axis = 1, keepdims = True)
    return (mfcc - mean) / (std + 1e-9)

In [5]:
def extract_mfcc(path, sr = 22050, n_mfcc = 20, max_len = 1300, normalize = True):
    try:
        y, sr = librosa.load(path, sr = sr)
        mfcc = librosa.feature.mfcc(y = y, sr = sr, n_mfcc = n_mfcc)

        if normalize:
            mfcc = z_score_normalize(mfcc)

        if mfcc.shape[1] < max_len:
            pad_width = max_len - mfcc.shape[1]
            mfcc = np.pad(mfcc, ((0, 0), (0, pad_width)), mode = 'constant')
        else:
            mfcc = mfcc[:, :max_len]
        
        return mfcc
    
    except Exception as e:
        print(f'Error processing {path}: {e}')
        return None

print(extract_mfcc('/hdd/data/adp_data/fma_small/147/147413.mp3').shape)
print(extract_mfcc('/hdd/data/adp_data/fma_small/141/141310.mp3').shape)

(20, 1300)
(20, 1300)


In [6]:
def process_paths(mp3_paths):
    results = []
    for path in mp3_paths:
        mfcc = extract_mfcc(path)
        if mfcc is not None:
            results.append((path, mfcc))
    return results

In [7]:
n_processes = 10
mp3_paths = collect_mp3_paths(root_dir)

chunks = np.array_split(mp3_paths, n_processes)

with mp.Pool(processes = n_processes) as pool:
    all_results = []
    for result in tqdm(pool.imap_unordered(process_paths, chunks), total = len(chunks)):
        all_results.extend(result)

print(f'총 MFCC 추출 수: {len(all_results)}')

  0%|          | 0/10 [00:00<?, ?it/s]

/tmp/ipykernel_2228495/561239819.py:3: UserWarning: PySoundFile failed. Trying audioread instead.
  y, sr = librosa.load(path, sr = sr)
/home/ubuntu/work_space/adp_hands_on/.adp_hands_on/lib/python3.10/site-packages/librosa/core/audio.py:184: FutureWarning: librosa.core.audio.__audioread_load
	Deprecated as of librosa version 0.10.0.
	It will be removed in librosa version 1.0.
  y, sr_native = __audioread_load(path, offset, duration, dtype)


Error processing /hdd/data/adp_data/fma_small/099/099134.mp3: 


[src/libmpg123/parse.c:do_readahead():1083] warning: Cannot read next header, a one-frame stream? Duh...
[src/libmpg123/layer3.c:INT123_do_layer3():1804] error: dequantization failed!
/tmp/ipykernel_2228495/561239819.py:3: UserWarning: PySoundFile failed. Trying audioread instead.
  y, sr = librosa.load(path, sr = sr)
/home/ubuntu/work_space/adp_hands_on/.adp_hands_on/lib/python3.10/site-packages/librosa/core/audio.py:184: FutureWarning: librosa.core.audio.__audioread_load
	Deprecated as of librosa version 0.10.0.
	It will be removed in librosa version 1.0.
  y, sr_native = __audioread_load(path, offset, duration, dtype)


Error processing /hdd/data/adp_data/fma_small/133/133297.mp3: 


...

Error processing /hdd/data/adp_data/fma_small/098/098565.mp3: 


Note: Illegal Audio-MPEG-Header 0x00000000 at offset 33361.
Note: Trying to resync...
Note: Skipped 1024 bytes in input.
[src/libmpg123/parse.c:wetwork():1349] error: Giving up resync after 1024 bytes - your stream is not nice... (maybe increasing resync limit could help).
[src/libmpg123/layer3.c:INT123_do_layer3():1804] error: dequantization failed!
[src/libmpg123/layer3.c:INT123_do_layer3():1844] error: dequantization failed!
[src/libmpg123/layer3.c:INT123_do_layer3():1774] error: part2_3_length (3360) too large for available bit count (3240)
[src/libmpg123/layer3.c:INT123_do_layer3():1774] error: part2_3_length (3328) too large for available bit count (3240)
/tmp/ipykernel_2228495/561239819.py:3: UserWarning: PySoundFile failed. Trying audioread instead.
  y, sr = librosa.load(path, sr = sr)
/home/ubuntu/work_space/adp_hands_on/.adp_hands_on/lib/python3.10/site-packages/librosa/core/audio.py:184: FutureWarning: librosa.core.audio.__audioread_load
	Deprecated as of librosa version 0.

Error processing /hdd/data/adp_data/fma_small/108/108925.mp3: 


[src/libmpg123/parse.c:do_readahead():1083] warning: Cannot read next header, a one-frame stream? Duh...


총 MFCC 추출 수: 7994


In [8]:
paths = [item[0] for item in all_results[:30]]
mfccs = [item[1].T for item in all_results[:30]]

n = len(mfccs)
dtw_matrix = np.zeros((n, n))

for i in tqdm(range(n)):
    for j in range(i + 1,  n):
        dist, _, _, _ = accelerated_dtw(mfccs[i], mfccs[j], dist = 'euclidean')
        dtw_matrix[i, j] = dtw_matrix[j, i] = dist

  0%|          | 0/30 [00:00<?, ?it/s]

In [ ]:
def find_top_k_similar(dtw_matrix, paths, target_idx = 0, k = 5):
    distances = dtw_matrix[target_idx]
    indices = np.argsort(distances)[1: k + 1]
    return [(paths[i], distances[i]) for i in indices]

top_k = find_top_k_similar(dtw_matrix, paths, target_idx = 5, k = 1)
for path, dist in top_k:
    print(f'{path} (DTW 거리: {dist: .2f})')

/hdd/data/adp_data/fma_small/152/152258.mp3 (DTW 거리:  7715.71)


In [11]:
print(paths[5])

/hdd/data/adp_data/fma_small/152/152324.mp3


In [13]:
song1 = '/hdd/data/adp_data/fma_small/152/152324.mp3'
song2 = '/hdd/data/adp_data/fma_small/152/152258.mp3'

y1, sr1 = librosa.load(song1, sr = None)
display(Audio(y1, rate = sr1))
y2, sr2 = librosa.load(song2, sr = None)
display(Audio(y2, rate = sr2))